In [1]:
#import relevant libraries
import os
import subprocess
import numpy as np
import pandas as pd
import sys; sys.path
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.metrics import explained_variance_score, r2_score
from sklearn.linear_model import Ridge

from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score, GroupKFold, GroupShuffleSplit

In [2]:
# read and clean HCP data
# set base dirctories
HCP_base_dir   = '/Users/elvishadhamala/Documents/yale/HCP/'

# load dataframes for the cortical areal-level properties
# suraface area, gray matter volume, and cortical thickness
HCP_surf_area_df = pd.read_csv(os.path.join(HCP_base_dir, 'group_net_surfarea_native_freesurfer.csv'))
HCP_gray_vol_df = pd.read_csv(os.path.join(HCP_base_dir, 'group_net_grayvol_native_freesurfer.csv'))
HCP_thick_df = pd.read_csv(os.path.join(HCP_base_dir, 'group_net_thickavg_native_freesurfer.csv'))

# load subj behavioural and family data
HCP_subj_data_df = pd.read_csv(os.path.join(HCP_base_dir, 'hcp_behaviour.csv'))
HCP_subj_fam_df = pd.read_csv(os.path.join(HCP_base_dir, 'hcp_restricted.csv'))
HCP_subj_fs_df = pd.read_csv(os.path.join(HCP_base_dir, 'hcp_freesurfer.csv'))

#create a mask for the subject and family data and only keep the ones that have the cortical areal-level properties 
HCP_mask_data=np.isin(HCP_subj_data_df.Subject, HCP_surf_area_df.id)
HCP_subj_data_df = HCP_subj_data_df[HCP_mask_data]

HCP_mask_fam=np.isin(HCP_subj_fam_df.Subject, HCP_surf_area_df.id)
HCP_subj_fam_df = HCP_subj_fam_df[HCP_mask_fam]

HCP_mask_fs=np.isin(HCP_subj_fs_df.Subject, HCP_surf_area_df.id)
HCP_subj_fs_df = HCP_subj_fs_df[HCP_mask_fs]


HCP_surf_area_df = HCP_surf_area_df.set_index(HCP_subj_data_df.index)
HCP_gray_vol_df = HCP_gray_vol_df.set_index(HCP_subj_data_df.index)
HCP_thick_df = HCP_thick_df.set_index(HCP_subj_data_df.index)
HCP_subj_fs_df = HCP_subj_fs_df.set_index(HCP_subj_data_df.index)


HCP_icv = pd.DataFrame(HCP_subj_fs_df.FS_InterCranial_Vol)

# drop the id and 'none' columns
HCP_surf_area_df = HCP_surf_area_df.drop(columns=['id', 'lh_None', 'rh_None'])
HCP_gray_vol_df = HCP_gray_vol_df.drop(columns=['id', 'lh_None', 'rh_None'])
HCP_thick_df = HCP_thick_df.drop(columns=['id', 'lh_None', 'rh_None'])



HCP_cog = HCP_subj_data_df[["CogFluidComp_Unadj", "CogEarlyComp_Unadj", "CogTotalComp_Unadj", "CogCrystalComp_Unadj",
                  "PicSeq_Unadj", "CardSort_Unadj", "Flanker_Unadj", "PMAT24_A_CR", "ReadEng_Unadj", 
                  "PicVocab_Unadj", "ProcSpeed_Unadj", "DDisc_AUC_40K", "VSPLOT_TC", "SCPT_SEN", "SCPT_SPEC", 
                  "IWRD_TOT", "ListSort_Unadj", "MMSE_Score", "Language_Task_Math_Avg_Difficulty_Level", 
                  "Language_Task_Story_Avg_Difficulty_Level", "Relational_Task_Acc", "WM_Task_Acc"]] 


col_headers_main = ['Fluid Composite', 'Early Composite', 'Total Composite',
               'Crystal Composite', 'Visual Episodic Memory', 'Cognitive Flexibility (Card Sort)',
               'Inhibition (Flanker)', 'Fluid Intelligence (PMAT)', 'Reading Decoding', 
               'Vocabulary Comprehension', 'Processing Speed', 'Delay Discounting',
               'Spatial Orientation', 'Sustained Attention - Sens.', 
               'Sustained Attention - Spec.', 'Verbal Episodic Memory', 
               'Working Memory (List Sorting)', 'Cognitive Status', 'Arithmetic',
               'Story Comprehension', 'Relational Processing', 'Working Memory (N-Back)']

HCP_cog.columns = col_headers_main

HCP_cog = HCP_cog[['Fluid Composite', 'Total Composite', 'Crystal Composite',
                     'Visual Episodic Memory', 'Cognitive Flexibility (Card Sort)',
                     'Inhibition (Flanker)', 'Reading Decoding', 'Vocabulary Comprehension', 
                     'Processing Speed', 'Working Memory (List Sorting)']]



#get rid of all the subjects with nans
HCP_mask = np.asarray([~HCP_cog.isna().any(axis=1)])
HCP_surf_area = HCP_surf_area_df[np.transpose(HCP_mask==True)]
HCP_gray_vol = HCP_gray_vol_df[np.transpose(HCP_mask==True)]
HCP_thick = HCP_thick_df[np.transpose(HCP_mask==True)]
HCP_icv = HCP_icv[np.transpose(HCP_mask==True)]
HCP_cog = HCP_cog[np.transpose(HCP_mask==True)]
HCP_fam = HCP_subj_fam_df.loc[np.transpose(HCP_mask==True)]
HCP_subj = HCP_subj_data_df.loc[np.transpose(HCP_mask==True)]

# get normalised measured (by icv)
HCP_surf_area_norm = pd.DataFrame(HCP_surf_area.values/HCP_icv.values, columns=HCP_surf_area.columns)
HCP_gray_vol_norm = pd.DataFrame(HCP_gray_vol.values/HCP_icv.values, columns=HCP_gray_vol.columns)
HCP_thick_norm = pd.DataFrame(HCP_thick.values/HCP_icv.values, columns=HCP_thick.columns)


HCP_surf_area = HCP_surf_area.set_index(HCP_subj.index)
HCP_gray_vol = HCP_gray_vol.set_index(HCP_subj.index)
HCP_thick = HCP_thick.set_index(HCP_subj.index)
HCP_surf_area_norm = HCP_surf_area_norm.set_index(HCP_subj.index)
HCP_gray_vol_norm = HCP_gray_vol_norm.set_index(HCP_subj.index)
HCP_thick_norm = HCP_thick_norm.set_index(HCP_subj.index)
HCP_fam = HCP_fam.set_index(HCP_subj.index)


#read in alpha values from optimised 'true' models
HCP_results_dir   = '/Users/elvishadhamala/Documents/yale/HCP_ABCD_preds_results/'

HCP_alpha_surfarea_m = np.load(os.path.join(HCP_results_dir, 'surfarea_alpha_HCP_m.npy'))
HCP_alpha_surfarea_norm_m = np.load(os.path.join(HCP_results_dir, 'surfarea_norm_alpha_HCP_m.npy'))
HCP_alpha_grayvol_m = np.load(os.path.join(HCP_results_dir, 'grayvol_alpha_HCP_m.npy'))
HCP_alpha_grayvol_norm_m = np.load(os.path.join(HCP_results_dir, 'grayvol_norm_alpha_HCP_m.npy'))
HCP_alpha_thick_m = np.load(os.path.join(HCP_results_dir, 'thick_alpha_HCP_m.npy'))
HCP_alpha_thick_norm_m = np.load(os.path.join(HCP_results_dir, 'thick_norm_alpha_HCP_m.npy'))

HCP_alpha_surfarea_f = np.load(os.path.join(HCP_results_dir, 'surfarea_alpha_HCP_f.npy'))
HCP_alpha_surfarea_norm_f = np.load(os.path.join(HCP_results_dir, 'surfarea_norm_alpha_HCP_f.npy'))
HCP_alpha_grayvol_f = np.load(os.path.join(HCP_results_dir, 'grayvol_alpha_HCP_f.npy'))
HCP_alpha_grayvol_norm_f = np.load(os.path.join(HCP_results_dir, 'grayvol_norm_alpha_HCP_f.npy'))
HCP_alpha_thick_f = np.load(os.path.join(HCP_results_dir, 'thick_alpha_HCP_f.npy'))
HCP_alpha_thick_norm_f = np.load(os.path.join(HCP_results_dir, 'thick_norm_alpha_HCP_f.npy'))


In [3]:
# read and clean up ABCD data
# set base dirctories
ABCD_base_dir   = '/Users/elvishadhamala/Documents/yale/ABCD'

# load dataframes for the cortical areal-level properties
# suraface area, gray matter volume, and cortical thickness 
ABCD_surf_area_df = pd.read_csv(os.path.join(ABCD_base_dir, 'ABCD_group_surfarea.csv'), header=None)
ABCD_gray_vol_df = pd.read_csv(os.path.join(ABCD_base_dir, 'ABCD_group_grayvol.csv'), header=None)
ABCD_thick_df = pd.read_csv(os.path.join(ABCD_base_dir, 'ABCD_group_thickavg.csv'), header=None)
ABCD_icv_df = pd.read_csv(os.path.join(ABCD_base_dir, 'ABCD_icv.csv'), header=None)

# load subj behavioural and family data
ABCD_subj = pd.read_csv(os.path.join(ABCD_base_dir, 'ABCD_1823_demo_cog.csv'))


ABCD_surf_area = ABCD_surf_area_df.T
ABCD_gray_vol = ABCD_gray_vol_df.T
ABCD_thick = ABCD_thick_df.T


# get normalised measured (by icv)
ABCD_surf_area_norm = pd.DataFrame(ABCD_surf_area.values/ABCD_icv_df.values, columns=ABCD_surf_area.columns)
ABCD_gray_vol_norm = pd.DataFrame(ABCD_gray_vol.values/ABCD_icv_df.values, columns=ABCD_gray_vol.columns)
ABCD_thick_norm = pd.DataFrame(ABCD_thick.values/ABCD_icv_df.values, columns=ABCD_thick.columns)


ABCD_cog = ABCD_subj
ABCD_cog = ABCD_cog.drop(columns=['subjectkey', 'src_subject_id', 'sex', 'race_ethnicity', 'site_id_l'])
ABCD_cog

col_headers_main = ['Vocabulary Comprehension', 'Inhibition (Flanker)', 'Working Memory (List Sorting)',
                   'Cognitive Flexibility (Card Sort)', 'Processing Speed', 'Visual Episodic Memory',
                   'Reading Decoding', 'Fluid Composite', 'Crystal Composite', 'Total Composite',
                   'RAVLT - Trial VI Correct', 'RAVLT - Trial VII Correct', 'WISC-V - Total Raw Score',
                   'LMT - % Correct', 'LMT - RT Correct', 'LMT Efficiency']

ABCD_cog.columns = col_headers_main

ABCD_cog = ABCD_cog[['Fluid Composite', 'Total Composite', 'Crystal Composite',
                     'Visual Episodic Memory', 'Cognitive Flexibility (Card Sort)',
                     'Inhibition (Flanker)', 'Reading Decoding', 'Vocabulary Comprehension', 
                     'Processing Speed', 'Working Memory (List Sorting)']]


#read in alpha values from optimised 'true' models
ABCD_results_dir   = '/Users/elvishadhamala/Documents/yale/HCP_ABCD_preds_results/'

ABCD_alpha_surfarea_m = np.load(os.path.join(ABCD_results_dir, 'surfarea_alpha_ABCD_m.npy'))
ABCD_alpha_surfarea_norm_m = np.load(os.path.join(ABCD_results_dir, 'surfarea_norm_alpha_ABCD_m.npy'))
ABCD_alpha_grayvol_m = np.load(os.path.join(ABCD_results_dir, 'grayvol_alpha_ABCD_m.npy'))
ABCD_alpha_grayvol_norm_m = np.load(os.path.join(ABCD_results_dir, 'grayvol_norm_alpha_ABCD_m.npy'))
ABCD_alpha_thick_m = np.load(os.path.join(ABCD_results_dir, 'thick_alpha_ABCD_m.npy'))
ABCD_alpha_thick_norm_m = np.load(os.path.join(ABCD_results_dir, 'thick_norm_alpha_ABCD_m.npy'))

ABCD_alpha_surfarea_f = np.load(os.path.join(ABCD_results_dir, 'surfarea_alpha_ABCD_f.npy'))
ABCD_alpha_surfarea_norm_f = np.load(os.path.join(ABCD_results_dir, 'surfarea_norm_alpha_ABCD_f.npy'))
ABCD_alpha_grayvol_f = np.load(os.path.join(ABCD_results_dir, 'grayvol_alpha_ABCD_f.npy'))
ABCD_alpha_grayvol_norm_f = np.load(os.path.join(ABCD_results_dir, 'grayvol_norm_alpha_ABCD_f.npy'))
ABCD_alpha_thick_f = np.load(os.path.join(ABCD_results_dir, 'thick_alpha_ABCD_f.npy'))
ABCD_alpha_thick_norm_f = np.load(os.path.join(ABCD_results_dir, 'thick_norm_alpha_ABCD_f.npy'))

In [4]:
# mask sex for HCP
mask_sex = HCP_subj.Gender=='M'
HCP_subj_m = HCP_subj[mask_sex]
HCP_surfarea_m = HCP_surf_area[mask_sex]
HCP_grayvol_m = HCP_gray_vol[mask_sex]
HCP_thick_m = HCP_thick[mask_sex]
HCP_surfarea_norm_m = HCP_surf_area_norm[mask_sex]
HCP_grayvol_norm_m = HCP_gray_vol_norm[mask_sex]
HCP_thick_norm_m = HCP_thick_norm[mask_sex]
HCP_fam_m = HCP_fam[mask_sex]
HCP_cog_m = HCP_cog[mask_sex]


mask_sex = HCP_subj.Gender=='F'
HCP_subj_f = HCP_subj[mask_sex]
HCP_surfarea_f = HCP_surf_area[mask_sex]
HCP_grayvol_f = HCP_gray_vol[mask_sex]
HCP_thick_f = HCP_thick[mask_sex]
HCP_surfarea_norm_f = HCP_surf_area_norm[mask_sex]
HCP_grayvol_norm_f = HCP_gray_vol_norm[mask_sex]
HCP_thick_norm_f = HCP_thick_norm[mask_sex]
HCP_fam_f = HCP_fam[mask_sex]
HCP_cog_f = HCP_cog[mask_sex]



In [5]:
# mask sex for ABCD

mask_sex = ABCD_subj.sex=='M'
ABCD_subj_m = ABCD_subj[mask_sex]
ABCD_surfarea_m = ABCD_surf_area[mask_sex]
ABCD_grayvol_m = ABCD_gray_vol[mask_sex]
ABCD_thick_m = ABCD_thick[mask_sex]
ABCD_surfarea_norm_m = ABCD_surf_area_norm[mask_sex]
ABCD_grayvol_norm_m = ABCD_gray_vol_norm[mask_sex]
ABCD_thick_norm_m = ABCD_thick_norm[mask_sex]
ABCD_cog_m = ABCD_cog[mask_sex]

mask_sex = ABCD_subj.sex=='F'
ABCD_subj_f = ABCD_subj[mask_sex]
ABCD_surfarea_f = ABCD_surf_area[mask_sex]
ABCD_grayvol_f = ABCD_gray_vol[mask_sex]
ABCD_thick_f = ABCD_thick[mask_sex]
ABCD_surfarea_norm_f = ABCD_surf_area_norm[mask_sex]
ABCD_grayvol_norm_f = ABCD_gray_vol_norm[mask_sex]
ABCD_thick_norm_f = ABCD_thick_norm[mask_sex]
ABCD_cog_f = ABCD_cog[mask_sex]


In [6]:
#number of repetitions you want to perform
rep = 10000
#number of folds you want in the cross-validation
k = 3
#proportion of data you want in your training set and test set
train_size = .66
test_size = 1-train_size


#set x data to be the input variable you want to use
X_HCP_m = HCP_thick_norm_m
X_ABCD_m = ABCD_thick_norm_m

Y_HCP_m = HCP_cog_m
Y_ABCD_m = ABCD_cog_m


X_HCP_f = HCP_thick_norm_f
X_ABCD_f = ABCD_thick_norm_f

Y_HCP_f = HCP_cog_f
Y_ABCD_f = ABCD_cog_f

#set alphas to be the alpha values from the optimised models
alphas_ABCD_m = ABCD_alpha_thick_norm_m
alphas_HCP_m = HCP_alpha_thick_norm_m

alphas_ABCD_f = ABCD_alpha_thick_norm_f
alphas_HCP_f = HCP_alpha_thick_norm_f

#number of variables you want to predict to be the number of variables stored in the cognition variablse
n_cog = Y_HCP_m.shape[1]

#number of features 
n_feat = X_HCP_m.shape[1]

#number of test sets
n_test = 4

In [7]:
#create arrays to store variables

#r^2 - coefficient of determination
r2_ABCD_m = np.zeros([rep,n_cog,n_test])
#explained variance
var_ABCD_m = np.zeros([rep,n_cog,n_test])
#correlation between true and predicted (aka prediction accuracy)
corr_ABCD_m = np.zeros([rep,n_cog,n_test])
#optimised alpha (hyperparameter)
rand_alpha_ABCD_m = np.zeros([rep,n_cog])


#r^2 - coefficient of determination
r2_ABCD_f = np.zeros([rep,n_cog,n_test])
#explained variance
var_ABCD_f = np.zeros([rep,n_cog,n_test])
#correlation between true and predicted (aka prediction accuracy)
corr_ABCD_f = np.zeros([rep,n_cog,n_test])
#optimised alpha (hyperparameter)
rand_alpha_ABCD_f = np.zeros([rep,n_cog])

#r^2 - coefficient of determination
r2_HCP_m = np.zeros([rep,n_cog,n_test])
#explained variance
var_HCP_m = np.zeros([rep,n_cog,n_test])
#correlation between true and predicted (aka prediction accuracy)
corr_HCP_m = np.zeros([rep,n_cog,n_test])
#optimised alpha (hyperparameter)
rand_alpha_HCP_m = np.zeros([rep,n_cog])


#r^2 - coefficient of determination
r2_HCP_f = np.zeros([rep,n_cog,n_test])
#explained variance
var_HCP_f = np.zeros([rep,n_cog,n_test])
#correlation between true and predicted (aka prediction accuracy)
corr_HCP_f = np.zeros([rep,n_cog,n_test])
#optimised alpha (hyperparameter)
rand_alpha_HCP_f = np.zeros([rep,n_cog])


In [8]:
#iterate through number of models
for p in range(rep):
    #print model # you're on
    print('Model %d' %(p+1))
    
    #randomly shuffle Y values to generate null distribution of predictions 
    Y_HCP_m_shuffle = Y_HCP_m.sample(frac=1)
    Y_HCP_f_shuffle = Y_HCP_f.sample(frac=1)
    Y_ABCD_m_shuffle = Y_ABCD_m.sample(frac=1)
    Y_ABCD_f_shuffle = Y_ABCD_f.sample(frac=1)
    
    #for HCP males
    #group split HCP male data into train and test sets, using family ID as group ccategory
    train_inds_HCP_m, test_inds_HCP_m = next(GroupShuffleSplit(test_size=1-train_size, n_splits=1, random_state = p).split(X_HCP_m, groups=HCP_fam_m['Family_ID']))
    
    #set x values based on indices from split
    x_train_HCP_m = X_HCP_m.iloc[train_inds_HCP_m].values
    x_test_HCP_m = X_HCP_m.iloc[test_inds_HCP_m].values
        
    #set y values for based on indices from split    
    cog_train_HCP_m = Y_HCP_m_shuffle.iloc[train_inds_HCP_m].values
    cog_test_HCP_m = Y_HCP_m_shuffle.iloc[test_inds_HCP_m].values
    
    #for HCP females
    #group split HCP female data into train and test sets, using family ID as group ccategory
    train_inds_HCP_f, test_inds_HCP_f = next(GroupShuffleSplit(test_size=1-train_size, n_splits=1, random_state = p).split(X_HCP_f, groups=HCP_fam_f['Family_ID']))
    
    #set x values based on indices from split
    x_train_HCP_f = X_HCP_f.iloc[train_inds_HCP_f].values
    x_test_HCP_f = X_HCP_f.iloc[test_inds_HCP_f].values
        
    #set y values for based on indices from split      
    cog_train_HCP_f = Y_HCP_f_shuffle.iloc[train_inds_HCP_f].values
    cog_test_HCP_f = Y_HCP_f_shuffle.iloc[test_inds_HCP_f].values
    
    
    #for ABCD males
    train_inds_ABCD_m, test_inds_ABCD_m = next(GroupShuffleSplit(test_size=1-train_size, n_splits=1, random_state = p).split(X_ABCD_m, groups=ABCD_subj_m['site_id_l']))
    
    #set x values based on indices from split
    x_train_ABCD_m = X_ABCD_m.iloc[train_inds_ABCD_m].values
    x_test_ABCD_m = X_ABCD_m.iloc[test_inds_ABCD_m].values
        
    #set y values for based on indices from split      
    cog_train_ABCD_m = Y_ABCD_m_shuffle.iloc[train_inds_ABCD_m].values
    cog_test_ABCD_m = Y_ABCD_m_shuffle.iloc[test_inds_ABCD_m].values    
    
    #for ABCD females
    train_inds_ABCD_f, test_inds_ABCD_f = next(GroupShuffleSplit(test_size=1-train_size, n_splits=1, random_state = p).split(X_ABCD_f, groups=ABCD_subj_f['site_id_l']))
    
    #set x values based on indices from split
    x_train_ABCD_f = X_ABCD_f.iloc[train_inds_ABCD_f].values
    x_test_ABCD_f = X_ABCD_f.iloc[test_inds_ABCD_f].values
        
    #set y values for based on indices from split      
    cog_train_ABCD_f = Y_ABCD_f_shuffle.iloc[train_inds_ABCD_f].values
    cog_test_ABCD_f = Y_ABCD_f_shuffle.iloc[test_inds_ABCD_f].values  
    
    
    #iterate through the cognitive metrics you want to predict
    for cog in range (n_cog):

        #print and set cognitive metrics being predicted 
        print ("Behaviour: %s" % Y_HCP_m.columns[cog])
    
        y_train_HCP_m = cog_train_HCP_m[:,cog]
        y_test_HCP_m = cog_test_HCP_m[:,cog]
        
        y_train_HCP_f = cog_train_HCP_f[:,cog]
        y_test_HCP_f = cog_test_HCP_f[:,cog]
        
        y_train_ABCD_m = cog_train_ABCD_m[:,cog]
        y_test_ABCD_m = cog_test_ABCD_m[:,cog]
        
        y_train_ABCD_f = cog_train_ABCD_f[:,cog]
        y_test_ABCD_f = cog_test_ABCD_f[:,cog]
        
        
        rand_alpha_HCP_m[p,cog] = np.random.choice(alphas_HCP_m[:,cog])
        rand_alpha_HCP_f[p,cog] = np.random.choice(alphas_HCP_f[:,cog])
        
        rand_alpha_ABCD_m[p,cog] = np.random.choice(alphas_ABCD_m[:,cog])
        rand_alpha_ABCD_f[p,cog] = np.random.choice(alphas_ABCD_f[:,cog])
        
        
        


        #fit model using optimised hyperparameter
        model_HCP_m = Ridge(alpha = rand_alpha_HCP_m[p,cog], normalize=True, max_iter=1000000, solver='lsqr')
        model_HCP_m.fit(x_train_HCP_m, y_train_HCP_m);
            
        model_HCP_f = Ridge(alpha = rand_alpha_HCP_f[p,cog], normalize=True, max_iter=1000000, solver='lsqr')
        model_HCP_f.fit(x_train_HCP_f, y_train_HCP_f);
        
        
        model_ABCD_m = Ridge(alpha = rand_alpha_ABCD_m[p,cog], normalize=True, max_iter=1000000, solver='lsqr')
        model_ABCD_m.fit(x_train_ABCD_m, y_train_ABCD_m);
        
        model_ABCD_f = Ridge(alpha = rand_alpha_ABCD_f[p,cog], normalize=True, max_iter=1000000, solver='lsqr')
        model_ABCD_f.fit(x_train_ABCD_f, y_train_ABCD_f);
        
        
        #compute r^2 (coefficient of determination)
        r2_HCP_m[p,cog,0]=model_HCP_m.score(x_test_HCP_m,y_test_HCP_m)
        r2_HCP_m[p,cog,1]=model_HCP_m.score(x_test_HCP_f,y_test_HCP_f)
        r2_HCP_m[p,cog,2]=model_HCP_m.score(x_test_ABCD_m,y_test_ABCD_m)
        r2_HCP_m[p,cog,3]=model_HCP_m.score(x_test_ABCD_f,y_test_ABCD_f)
        
        r2_HCP_f[p,cog,0]=model_HCP_f.score(x_test_HCP_m,y_test_HCP_m)
        r2_HCP_f[p,cog,1]=model_HCP_f.score(x_test_HCP_f,y_test_HCP_f)
        r2_HCP_f[p,cog,2]=model_HCP_f.score(x_test_ABCD_m,y_test_ABCD_m)
        r2_HCP_f[p,cog,3]=model_HCP_f.score(x_test_ABCD_f,y_test_ABCD_f)
        
        r2_ABCD_m[p,cog,0]=model_ABCD_m.score(x_test_HCP_m,y_test_HCP_m)
        r2_ABCD_m[p,cog,1]=model_ABCD_m.score(x_test_HCP_f,y_test_HCP_f)
        r2_ABCD_m[p,cog,2]=model_ABCD_m.score(x_test_ABCD_m,y_test_ABCD_m)
        r2_ABCD_m[p,cog,3]=model_ABCD_m.score(x_test_ABCD_f,y_test_ABCD_f)
        
        r2_ABCD_f[p,cog,0]=model_ABCD_f.score(x_test_HCP_m,y_test_HCP_m)
        r2_ABCD_f[p,cog,1]=model_ABCD_f.score(x_test_HCP_f,y_test_HCP_f)
        r2_ABCD_f[p,cog,2]=model_ABCD_f.score(x_test_ABCD_m,y_test_ABCD_m)
        r2_ABCD_f[p,cog,3]=model_ABCD_f.score(x_test_ABCD_f,y_test_ABCD_f)
        
        
        preds_HCP_m = []
        preds_HCP_f = []
        preds_ABCD_m = []
        preds_ABCD_f = []

        #generate predictions from HCP m model
        preds_HCP_m = model_HCP_m.predict(x_test_HCP_m).ravel()
        preds_HCP_f = model_HCP_m.predict(x_test_HCP_f).ravel()
        preds_ABCD_m = model_HCP_m.predict(x_test_ABCD_m).ravel()
        preds_ABCD_f = model_HCP_m.predict(x_test_ABCD_f).ravel()
        
        #compute explained variance 
        var_HCP_m[p,cog,0] = explained_variance_score(y_test_HCP_m, preds_HCP_m)
        var_HCP_m[p,cog,1] = explained_variance_score(y_test_HCP_f, preds_HCP_f)
        var_HCP_m[p,cog,2] = explained_variance_score(y_test_ABCD_m, preds_ABCD_m)
        var_HCP_m[p,cog,3] = explained_variance_score(y_test_ABCD_f, preds_ABCD_f)

        #compute correlation between true and predicted (prediction accuracy)
        corr_HCP_m[p,cog,0] = np.corrcoef(y_test_HCP_m.ravel(), preds_HCP_m)[1,0]
        corr_HCP_m[p,cog,1] = np.corrcoef(y_test_HCP_f.ravel(), preds_HCP_f)[1,0]
        corr_HCP_m[p,cog,2] = np.corrcoef(y_test_ABCD_m.ravel(), preds_ABCD_m)[1,0]
        corr_HCP_m[p,cog,3] = np.corrcoef(y_test_ABCD_f.ravel(), preds_ABCD_f)[1,0]
        
        preds_HCP_m = []
        preds_HCP_f = []
        preds_ABCD_m = []
        preds_ABCD_f = []

        #generate predictions from HCP f model
        preds_HCP_m = model_HCP_f.predict(x_test_HCP_m).ravel()
        preds_HCP_f = model_HCP_f.predict(x_test_HCP_f).ravel()
        preds_ABCD_m = model_HCP_f.predict(x_test_ABCD_m).ravel()
        preds_ABCD_f = model_HCP_f.predict(x_test_ABCD_f).ravel()
        
        #compute explained variance 
        var_HCP_f[p,cog,0] = explained_variance_score(y_test_HCP_m, preds_HCP_m)
        var_HCP_f[p,cog,1] = explained_variance_score(y_test_HCP_f, preds_HCP_f)
        var_HCP_f[p,cog,2] = explained_variance_score(y_test_ABCD_m, preds_ABCD_m)
        var_HCP_f[p,cog,3] = explained_variance_score(y_test_ABCD_f, preds_ABCD_f)

        #compute correlation between true and predicted (prediction accuracy)
        corr_HCP_f[p,cog,0] = np.corrcoef(y_test_HCP_m.ravel(), preds_HCP_m)[1,0]
        corr_HCP_f[p,cog,1] = np.corrcoef(y_test_HCP_f.ravel(), preds_HCP_f)[1,0]
        corr_HCP_f[p,cog,2] = np.corrcoef(y_test_ABCD_m.ravel(), preds_ABCD_m)[1,0]
        corr_HCP_f[p,cog,3] = np.corrcoef(y_test_ABCD_f.ravel(), preds_ABCD_f)[1,0]
        
        preds_HCP_m = []
        preds_HCP_f = []
        preds_ABCD_m = []
        preds_ABCD_f = []

        #generate predictions from ABCD m model
        preds_HCP_m = model_ABCD_m.predict(x_test_HCP_m).ravel()
        preds_HCP_f = model_ABCD_m.predict(x_test_HCP_f).ravel()
        preds_ABCD_m = model_ABCD_m.predict(x_test_ABCD_m).ravel()
        preds_ABCD_f = model_ABCD_m.predict(x_test_ABCD_f).ravel()
        
        #compute explained variance 
        var_ABCD_m[p,cog,0] = explained_variance_score(y_test_HCP_m, preds_HCP_m)
        var_ABCD_m[p,cog,1] = explained_variance_score(y_test_HCP_f, preds_HCP_f)
        var_ABCD_m[p,cog,2] = explained_variance_score(y_test_ABCD_m, preds_ABCD_m)
        var_ABCD_m[p,cog,3] = explained_variance_score(y_test_ABCD_f, preds_ABCD_f)

        #compute correlation between true and predicted (prediction accuracy)
        corr_ABCD_m[p,cog,0] = np.corrcoef(y_test_HCP_m.ravel(), preds_HCP_m)[1,0]
        corr_ABCD_m[p,cog,1] = np.corrcoef(y_test_HCP_f.ravel(), preds_HCP_f)[1,0]
        corr_ABCD_m[p,cog,2] = np.corrcoef(y_test_ABCD_m.ravel(), preds_ABCD_m)[1,0]
        corr_ABCD_m[p,cog,3] = np.corrcoef(y_test_ABCD_f.ravel(), preds_ABCD_f)[1,0]
        
        
        preds_HCP_m = []
        preds_HCP_f = []
        preds_ABCD_m = []
        preds_ABCD_f = []

        #generate predictions from HCP f model
        preds_HCP_m = model_ABCD_f.predict(x_test_HCP_m).ravel()
        preds_HCP_f = model_ABCD_f.predict(x_test_HCP_f).ravel()
        preds_ABCD_m = model_ABCD_f.predict(x_test_ABCD_m).ravel()
        preds_ABCD_f = model_ABCD_f.predict(x_test_ABCD_f).ravel()
        
        #compute explained variance 
        var_ABCD_f[p,cog,0] = explained_variance_score(y_test_HCP_m, preds_HCP_m)
        var_ABCD_f[p,cog,1] = explained_variance_score(y_test_HCP_f, preds_HCP_f)
        var_ABCD_f[p,cog,2] = explained_variance_score(y_test_ABCD_m, preds_ABCD_m)
        var_ABCD_f[p,cog,3] = explained_variance_score(y_test_ABCD_f, preds_ABCD_f)

        #compute correlation between true and predicted (prediction accuracy)
        corr_ABCD_f[p,cog,0] = np.corrcoef(y_test_HCP_m.ravel(), preds_HCP_m)[1,0]
        corr_ABCD_f[p,cog,1] = np.corrcoef(y_test_HCP_f.ravel(), preds_HCP_f)[1,0]
        corr_ABCD_f[p,cog,2] = np.corrcoef(y_test_ABCD_m.ravel(), preds_ABCD_m)[1,0]
        corr_ABCD_f[p,cog,3] = np.corrcoef(y_test_ABCD_f.ravel(), preds_ABCD_f)[1,0]
        
 

Model 1
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 2
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 3
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sort

Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 26
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 27
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 28
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Compre

Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 51
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 52
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 53
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic

Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 76
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 77
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 78
Behaviour: Fluid Composite
Behaviour: Total Co

Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 100
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 101
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 102
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Com

...

Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9894
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9895
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9896
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Ep

Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9919
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9920
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9921
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Rea

Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9944
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9945
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9946
Behaviour: Fluid Composite
Behaviour: To

Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9969
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9970
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9971
Behaviour: Fluid Composite
Behaviour: To

Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9993
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9994
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibition (Flanker)
Behaviour: Reading Decoding
Behaviour: Vocabulary Comprehension
Behaviour: Processing Speed
Behaviour: Working Memory (List Sorting)
Model 9995
Behaviour: Fluid Composite
Behaviour: Total Composite
Behaviour: Crystal Composite
Behaviour: Visual Episodic Memory
Behaviour: Cognitive Flexibility (Card Sort)
Behaviour: Inhibit

In [9]:
# save results
base_dir  = '/Users/elvishadhamala/Documents/yale/HCP_ABCD_preds_results'

np.save(os.path.join(base_dir, 'null_thick_norm_r2_HCP_m.npy'),r2_HCP_m)
np.save(os.path.join(base_dir, 'null_thick_norm_var_HCP_m.npy'),var_HCP_m)
np.save(os.path.join(base_dir, 'null_thick_norm_corr_HCP_m.npy'),corr_HCP_m)
np.save(os.path.join(base_dir, 'null_thick_norm_alpha_HCP_m.npy'),rand_alpha_HCP_m)


np.save(os.path.join(base_dir, 'null_thick_norm_r2_HCP_f.npy'),r2_HCP_f)
np.save(os.path.join(base_dir, 'null_thick_norm_var_HCP_f.npy'),var_HCP_f)
np.save(os.path.join(base_dir, 'null_thick_norm_corr_HCP_f.npy'),corr_HCP_f)
np.save(os.path.join(base_dir, 'null_thick_norm_alpha_HCP_f.npy'),rand_alpha_HCP_f)



np.save(os.path.join(base_dir, 'null_thick_norm_r2_ABCD_m.npy'),r2_ABCD_m)
np.save(os.path.join(base_dir, 'null_thick_norm_var_ABCD_m.npy'),var_ABCD_m)
np.save(os.path.join(base_dir, 'null_thick_norm_corr_ABCD_m.npy'),corr_ABCD_m)
np.save(os.path.join(base_dir, 'null_thick_norm_alpha_ABCD_m.npy'),rand_alpha_ABCD_m)


np.save(os.path.join(base_dir, 'null_thick_norm_r2_ABCD_f.npy'),r2_ABCD_f)
np.save(os.path.join(base_dir, 'null_thick_norm_var_ABCD_f.npy'),var_ABCD_f)
np.save(os.path.join(base_dir, 'null_thick_norm_corr_ABCD_f.npy'),corr_ABCD_f)
np.save(os.path.join(base_dir, 'null_thick_norm_alpha_ABCD_f.npy'),rand_alpha_ABCD_f)

